# Import Data/Pkg, Process Data

In [2]:
using Pkg, CategoricalArrays, CSV, DataFrames, Statistics
using StatsBase

In [3]:
data = CSV.read("train.csv", DataFrame);

In [4]:
df = data;

In [5]:
df

381109×12 DataFrame
    Row │ id      Gender   Age    Driving_License  Region_Code  Previously_Ins ⋯
        │ Int64   String7  Int64  Int64            Float64      Int64          ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │      1  Male        44                1         28.0                 ⋯
      2 │      2  Male        76                1          3.0
      3 │      3  Male        47                1         28.0
      4 │      4  Male        21                1         11.0
      5 │      5  Female      29                1         41.0                 ⋯
      6 │      6  Female      24                1         33.0
      7 │      7  Male        23                1         11.0
      8 │      8  Female      56                1         28.0
      9 │      9  Female      24                1          3.0                 ⋯
     10 │     10  Female      32                1          6.0
     11 │     11  Female      47                1         35.0
   ⋮    │   ⋮        ⋮       ⋮           ⋮              ⋮               ⋮      ⋱
 381100 │ 381100  Female      51                1         28.0
 381101 │ 381101  Female      29                1         28.0                 ⋯
 381102 │ 381102  Female      70                1         28.0
 381103 │ 381103  Female      25                1         41.0
 381104 │ 381104  Male        47                1         50.0
 381105 │ 381105  Male        74                1         26.0                 ⋯
 381106 │ 381106  Male        30                1         37.0
 381107 │ 381107  Male        21                1         30.0
 381108 │ 381108  Female      68                1         14.0
 381109 │ 381109  Male        46                1         29.0                 ⋯
                                               7 columns and 381088 rows omitted

In [ ]:
# cat_sales = sort(combine(groupby(df, :Policy_Sales_Channel), nrow => :count), :count, rev=true)[1:5, :Policy_Sales_Channel]
# cat_regions = sort(combine(groupby(df, :Region_Code), nrow => :count), :count, rev=true)[1:5, :Region_Code]
# print(cat_sales, cat_regions)

In [9]:
# df.Region_Code = map(x -> x in cat_regions ? x : 0.0, df.Region_Code);
# df.Policy_Sales_Channel = map(x -> x in cat_sales ? x : 0.0, df.Policy_Sales_Channel);

# first(df, 5);

In [6]:
df.Vehicle_Damage = map(x -> x == "Yes" ? 1 : 0, df.Vehicle_Damage);
df.Vehicle_Age = map(x -> x == "> 2 Years" ? 2 : x == "1-2 Year" ? 1 : 0, df.Vehicle_Age);
# df[!, "Region_Code"] = categorical(df[!,  "Region_Code"])
# df[!, "Policy_Sales_Channel"] = categorical(df[!, "Policy_Sales_Channel"])
df[!, "Gender"] = categorical(df[!, "Gender"])
df[!, "Annual_Premium"] = df[!, "Annual_Premium"].*0.012;

In [7]:
# df = df[df.Annual_Premium .<= 1000, :]; #379151

## Split Data

In [7]:
seed = 12345; 
X = df[:, Not([:Response, :Annual_Premium, :id, :Region_Code, :Policy_Sales_Channel])]
y = df.Response
t = df.Annual_Premium
(train_X, train_t, train_y), (test_X, test_t, test_y) = IAI.split_data(
    :policy_maximize, X, t, y, train_proportion=0.5, seed=seed);

In [8]:
train_t_discrete = [min(round(x, digits=-2), 1000) < 100 ? 100.0 : min(round(x, digits=-2), 1000) for x in train_t]
test_t_discrete = [min(round(x, digits=-2), 1000) < 100.0 ? 100.0 : min(round(x, digits=-2), 1000) for x in test_t];

In [9]:
# counts = countmap(train_t_discrete);

In [10]:
# print(countmap(train_y))
# print(countmap(test_y));

## Reward Estimator Set Up

In [11]:
t_options = 100:100:1000

100:100:1000

In [14]:
reward_lnr_dir_xgb = IAI.NumericClassificationRewardEstimator(
    outcome_estimator=IAI.XGBoostClassifier(num_round=50),
    outcome_insample_num_folds=5,
    reward_estimator=:direct_method,
    random_seed=12345,
)

Unfitted NumericClassificationRewardEstimator:
  outcome_estimator: Unfitted XGBoostClassifier:
    num_round: 50
  reward_estimator:  direct_method
  random_seed:       12345

In [15]:
reward_lnr_dir_rf = IAI.NumericClassificationRewardEstimator(
    outcome_estimator=IAI.RandomForestClassifier(max_depth=5),
    outcome_insample_num_folds=5,
    reward_estimator=:direct_method,
    random_seed=12345,
)

Unfitted NumericClassificationRewardEstimator:
  outcome_estimator: Unfitted RandomForestClassifier:
    max_depth: 5
  reward_estimator:  direct_method
  random_seed:       12345

In [16]:
reward_lnr_dr_xgb = IAI.NumericClassificationRewardEstimator( #t?
    propensity_estimator = IAI.XGBoostRegressor(num_round=50),
    outcome_estimator = IAI.XGBoostClassifier(num_round=50), #y
    reward_estimator = "doubly_robust",
    outcome_insample_num_folds=5,
    propensity_min_value = 0.1,
    random_seed = 12345,
)

Unfitted NumericClassificationRewardEstimator:
  propensity_estimator: Unfitted XGBoostRegressor:
    num_round: 50
  propensity_min_value: 0.1
  outcome_estimator:    Unfitted XGBoostClassifier:
    num_round: 50
  reward_estimator:     doubly_robust
  random_seed:          12345

In [17]:
reward_lnr_dr_rf = IAI.NumericClassificationRewardEstimator( #t?
    propensity_estimator = IAI.RandomForestRegressor(max_depth=5),
    outcome_estimator = IAI.RandomForestClassifier(max_depth=5), #y
    reward_estimator = "doubly_robust",
    outcome_insample_num_folds=5,
    propensity_min_value = 0.1,
    random_seed = 12345,
)

Unfitted NumericClassificationRewardEstimator:
  propensity_estimator: Unfitted RandomForestRegressor:
    max_depth: 5
  propensity_min_value: 0.1
  outcome_estimator:    Unfitted RandomForestClassifier:
    max_depth: 5
  reward_estimator:     doubly_robust
  random_seed:          12345

In [18]:
function get_rewards(reward_lnr, X, t, y, t_options)
  predictions, score = IAI.fit_predict!(reward_lnr, X, t, y, t_options,
                                        outcome_score_criterion=:auc)
  rewards = predictions[:reward]
  for t in t_options
    rewards[!, Symbol(t)] = round.(rewards[!, Symbol(t)] .* t, digits=3)
  end
  rewards, score
end

get_rewards (generic function with 1 method)

## Test Set AUC

In [34]:
test_rewards, test_reward_score = get_rewards(reward_lnr_dir_xgb, test_X, test_t_discrete, test_y, t_options)
test_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.869977
  "400"  => 0.843716
  "1000" => 0.800922
  "600"  => 0.798187
  "800"  => 0.783212
  "700"  => 0.795677
  "100"  => 0.781054
  "200"  => 0.89124
  "500"  => 0.816521
  "900"  => 0.748684

In [35]:
test_rewards, test_reward_score = get_rewards(reward_lnr_dir_rf, test_X, test_t_discrete, test_y, t_options)
test_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.881699
  "400"  => 0.854304
  "1000" => 0.809564
  "600"  => 0.816512
  "800"  => 0.788449
  "700"  => 0.806562
  "100"  => 0.796361
  "200"  => 0.89815
  "500"  => 0.829591
  "900"  => 0.808383

In [37]:
test_rewards, test_reward_score = get_rewards(reward_lnr_dr_xgb, test_X, test_t_discrete, test_y, t_options)
test_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.874841
  "400"  => 0.84849
  "1000" => 0.812676
  "600"  => 0.802744
  "800"  => 0.777809
  "700"  => 0.793584
  "100"  => 0.782963
  "200"  => 0.883945
  "500"  => 0.821938
  "900"  => 0.76231

In [36]:
test_rewards, test_reward_score = get_rewards(reward_lnr_dr_rf, test_X, test_t_discrete, test_y, t_options)
test_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.881381
  "400"  => 0.854078
  "1000" => 0.824017
  "600"  => 0.816972
  "800"  => 0.797826
  "700"  => 0.810361
  "100"  => 0.794812
  "200"  => 0.899496
  "500"  => 0.827918
  "900"  => 0.785778

In [39]:
test_rewards

190555×10 DataFrame
    Row │ 100      200      300       400       500       600        700       ⋯
        │ Float64  Float64  Float64   Float64   Float64   Float64    Float64   ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │  29.865   16.921   110.057   107.342  1638.57     244.697  493.968   ⋯
      2 │   7.636   32.63     97.837   180.825  1825.6      314.731  129.595
      3 │   0.037    0.116    -0.504     0.121     0.058      0.028    0.115
      4 │   0.034    0.021    -0.024     0.088     0.239      0.144    0.076
      5 │   3.921   28.413  -125.619    48.655    89.693    109.695   67.273   ⋯
      6 │  23.287   62.726    60.576  1479.33     95.017    139.353  152.508
      7 │   0.2      0.036     0.07      0.094     0.048     -0.622    0.069
      8 │   0.012    0.017     0.024     0.049     0.04      -2.078    2.423
      9 │ 316.823  151.24     99.589   147.54    203.216    252.131  255.689   ⋯
     10 │  17.942   67.495    72.601  1048.28     89.998    130.752  105.397
     11 │  15.245   21.17     63.028    83.169  -496.56      90.318   96.414
   ⋮    │    ⋮        ⋮        ⋮         ⋮         ⋮          ⋮         ⋮      ⋱
 190546 │ -79.608   47.969   138.228   156.819   207.641    190.219  185.477
 190547 │   0.407    0.06      0.016     0.284    -0.403      0.028    0.437   ⋯
 190548 │  26.402  125.642   109.342   140.521   176.335   6139.43   236.908
 190549 │  10.229    1.873    31.337  -204.076   134.297     70.446   18.81
 190550 │  20.898   24.569    87.138   112.365   159.189  -2666.69   261.775
 190551 │   6.956    8.328    56.555    88.169    92.843   -389.175  395.192   ⋯
 190552 │  -1.8      0.056     0.362     2.28      4.727      0.062    0.329
 190553 │  27.435   23.33     94.889   157.723  -556.634    356.675  233.737
 190554 │  13.804    9.43     35.145    70.681  -355.766    337.978   92.941
 190555 │   1.608    1.578     9.826    10.651   -32.949     41.587    3.036   ⋯
                                               3 columns and 190534 rows omitted

## Prescriptive Tree

In [13]:
prescriptive_grid = IAI.GridSearch(
    IAI.OptimalTreePrescriptionMaximizer(
      random_seed=1,
    ),
    max_depth=3:6,
)
# multiple the t(price)revenue with binary var y(1,0) buy or not buy
train_y_revenue = train_y .* train_t_discrete;

In [14]:
IAI.fit!(prescriptive_grid, train_X, train_t_discrete, train_y_revenue)

All Grid Results:

 Row │ max_depth  cp           train_score  valid_score  rank_valid_score 
     │ Int64      Float64      Float64      Float64      Int64            
─────┼────────────────────────────────────────────────────────────────────
   1 │         3  0.000299054    0.0907691    0.0589826                 4
   2 │         4  3.7678e-6      0.10362      0.0694228                 3
   3 │         5  9.22617e-5     0.120221     0.0814773                 2
   4 │         6  0.000135762    0.145032     0.09585                   1

Best Params:
  cp => 0.00013576241430462987
  max_depth => 6

Best Model - Fitted OptimalTreePrescriptionMaximizer:
  1) Split: Age < 29.5
    2) Split: Vehicle_Age is 0 or is missing
      3) Split: Gender is Male or is missing
        4) Split: Vintage < 113.5
          5) Split: Previously_Insured < 0.5
            6) Split: Vintage < 56.5
              7) Prescribe: 800.0, 1792 points, error 0.000004753
              8) Prescribe: 900.0, 2125 points, error 0.000002601
            9) Prescribe: 500.0, 7905 points, error 0.000003065
          10) Split: Vintage < 239.5
            11) Split: Previously_Insured < 0.5
              12) Prescribe: 900.0, 4708 points, error 0.000004957
              13) Prescribe: 800.0, 9239 points, error 0.000003057
            14) Split: Vintage < 253.5
              15) Prescribe: 900.0, 1580 points, error 0.000002572
              16) Prescribe: 800.0, 5298 points, error 0.000003659
        17) Split: Previously_Insured < 0.5
          18) Split: Vintage < 40.5
            19) Split: Age < 20.5
              20) Prescribe: 300.0, 90 points, error 0.000003216
              21) Prescribe: 1000.0, 1300 points, error 0.000001552
            22) Split: Vintage < 272.5
              23) Prescribe: 1000.0, 10516 points, error 0.000004359
              24) Prescribe: 1000.0, 1249 points, error 0.0000017
          25) Prescribe: 600.0, 28540 points, error 0.00000306
      26) Split: Age < 27.5
        27) Split: Age < 24.5
          28) Split: Vintage < 294.5
            29) Split: Age < 22.5
              30) Prescribe: 900.0, 803 points, error 0.000002505
              31) Prescribe: 1000.0, 490 points, error 0.000002636
            32) Prescribe: 500.0, 29 points, error 0.000004176
          33) Split: Vintage < 58.5
            34) Prescribe: 600.0, 130 points, error 0.000005123
            35) Prescribe: 1000.0, 663 points, error 0.000002781
        36) Prescribe: 900.0, 1010 points, error 0.000003144
    37) Split: Vehicle_Age in [0,1] or is missing
      38) Split: Previously_Insured < 0.5
        39) Split: Age < 52.5
          40) Split: Vehicle_Damage is 1 or is missing
            41) Split: Vintage < 99.5
              42) Prescribe: 900.0, 13541 points, error 0.000007043
              43) Prescribe: 1000.0, 29623 points, error 0.000007011
            44) Split: Vintage < 53.5
              45) Prescribe: 1000.0, 760 points, error 0
              46) Prescribe: 1000.0, 3901 points, error 0.00000361
          47) Split: Age < 62.5
            48) Split: Age < 57.5
              49) Prescribe: 900.0, 6830 points, error 0.0000069
              50) Prescribe: 1000.0, 4855 points, error 0.000006081
            51) Split: Vintage < 175.5
              52) Prescribe: 900.0, 5386 points, error 0.00000563
              53) Prescribe: 1000.0, 4018 points, error 0.000005591
        54) Prescribe: 800.0, 36209 points, error 0.000003078
      55) Split: Age < 59.5
        56) Split: Vintage < 96.5
          57) Split: Vintage < 34.5
            58) Split: Vintage < 19.5
              59) Prescribe: 900.0, 156 points, error 0.000008899
              60) Prescribe: 900.0, 277 points, error 0.000006483
            61) Split: Vintage < 36.5
              62) Prescribe: 1000.0, 41 points, error 0.000004606
              63) Prescribe: 1000.0, 1067 points, error 0.00000628
          64) Split: Age < 48.5
            65) Split: Age < 40.5
              66) Prescribe: 1000.0, 4

In [15]:
pred_treatments, pred_outcomes = IAI.predict(prescriptive_grid, test_X)

([900.0, 900.0, 800.0, 600.0, 900.0, 900.0, 600.0, 800.0, 1000.0, 1000.0  …  1000.0, 800.0, 1000.0, 1000.0, 1000.0, 1000.0, 600.0, 1000.0, 800.0, 1000.0], [771.4285714285713, 900.0, 8.333333333333258, 0.4329004329003965, 450.0, 242.30769230769215, 0.4329004329003965, 1.512287334593566, 369.69696969696975, 361.70212765957444  …  369.69696969696975, 1.512287334593566, 369.69696969696975, 666.6666666666667, 111.1111111111112, 666.6666666666667, 0.4329004329003965, 369.69696969696975, 299.9999999999999, 111.1111111111112])

In [16]:
IAI.predict_outcomes(prescriptive_grid, test_X)

190555×10 DataFrame
    Row │ 100.0      200.0      300.0        400.0        500.0       600.0    ⋯
        │ Float64    Float64    Float64      Float64      Float64     Float64  ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │ 32.7273    72.7273    120.0        150.968      201.863     243.529  ⋯
      2 │ 38.6364     0.0        72.0        136.986      197.368     173.684
      3 │  0.108696   0.0         0.349243     0.650195     0.0         0.0
      4 │  0.0        0.169205    0.0338983    0.0841308    0.0         0.4329
      5 │  2.31214    0.0        13.4434      17.1206       7.96813    29.1262 ⋯
      6 │ 22.0246    32.3529     74.0088      99.3913     117.159     146.403
      7 │  0.0        0.169205    0.0338983    0.0841308    0.0         0.4329
      8 │  0.131234   0.0         0.507543     0.769305     0.317158    0.2126
      9 │ 27.904     70.3797     99.0538     129.601      166.216     198.92   ⋯
     10 │ 18.2626    38.0952     63.0332      78.5546      91.9715    124.294
     11 │ 11.9238    30.7692     46.6847      55.1311      68.8073     66.5563
   ⋮    │     ⋮          ⋮           ⋮            ⋮           ⋮           ⋮    ⋱
 190546 │ 27.904     70.3797     99.0538     129.601      166.216     198.92
 190547 │  0.131234   0.0         0.507543     0.769305     0.317158    0.2126 ⋯
 190548 │ 27.904     70.3797     99.0538     129.601      166.216     198.92
 190549 │ 15.2381     0.0        40.2985      56.2963      90.5797    141.176
 190550 │  8.82894   12.5874     25.2503      37.4201      41.4491     55.036
 190551 │ 15.2381     0.0        40.2985      56.2963      90.5797    141.176  ⋯
 190552 │  0.0        0.169205    0.0338983    0.0841308    0.0         0.4329
 190553 │ 27.904     70.3797     99.0538     129.601      166.216     198.92
 190554 │ 13.3333     0.0         0.0         86.4865      68.9655     26.087
 190555 │  7.01139    5.71429    17.7515      19.4252      20.938      23.5808 ⋯
                                               5 columns and 190534 rows omitted

## OPT

## Numeric CLassification Reward Estimatro

In [19]:
train_rewards, train_reward_score = get_rewards(reward_lnr_dir_xgb, train_X, train_t_discrete, train_y, t_options)
train_rewards

[ Warning: This copy of Interpretable AI software is for academic purposes only and not for commercial use.
┌ Warning: Interpretable AI license expires soon: 2023-12-31T00:00:00. If you need to renew, please send us the following machine ID:
└ 44fca02ebc99c5087b23b281fd5bb2da3a62bf43dc5671731365c5cfc227d71a


190554×10 DataFrame
    Row │ 100      200      300      400      500      600      700      800   ⋯
        │ Float64  Float64  Float64  Float64  Float64  Float64  Float64  Float ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │   1.214   28.102    1.433    1.194    1.63     5.308    0.944    0.5 ⋯
      2 │   8.828   16.482   22.5     38.189   35.119   58.287   76.438   56.4
      3 │   0.008    0.04     0.018    0.043    0.261    0.098    0.069    0.5
      4 │   0.009    0.024    0.016    0.317    1.955    0.101    0.091    0.0
      5 │  26.581   71.941  149.828  122.385  236.015  151.564  497.561  149.7 ⋯
      6 │   0.035    0.025    0.086    1.125    0.041    1.521    0.116    0.6
      7 │  48.504    3.498   37.214   31.007  322.664  127.345   91.038   36.5
      8 │   8.862    8.883   24.784   29.223   61.309   49.355  100.654  152.3
      9 │   0.01     0.045    0.026    0.384    0.024    0.09     0.035    0.5 ⋯
     10 │  31.956    9.437  128.818  122.706  111.611  167.905  133.858  618.3
     11 │  22.298   40.718   89.069  114.24   165.09   192.508  284.571  419.1
   ⋮    │    ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋱
 190545 │   0.028    0.01     0.032    0.637    0.038    0.051    0.097    0.8
 190546 │   0.133    0.024    0.093    1.828    0.068    0.074    0.117   27.3 ⋯
 190547 │   0.038    0.146    0.019    0.059    0.038    0.03     0.121    0.2
 190548 │  34.197   76.655   91.268  120.182  199.984  210.579  176.447  151.6
 190549 │  26.881   28.822   63.936   96.093  150.014  113.114   69.56   339.8
 190550 │  26.581   23.346  127.814  114.822  153.583  169.536  213.809  393.4 ⋯
 190551 │  28.902   32.377   64.579   94.278  139.731  144.361  342.093  289.2
 190552 │   0.019    0.14     0.156    0.076    0.021    0.027    0.068    0.5
 190553 │   0.032    0.012    0.031    1.973    0.067    0.158    0.129    0.5
 190554 │   0.018    0.025    0.03     0.067    0.035    0.099    0.154    0.4 ⋯
                                               3 columns and 190533 rows omitted

In [20]:
train_rewards2, train_reward_score2 = get_rewards(reward_lnr_dir_rf, train_X, train_t_discrete, train_y, t_options)
train_rewards2

190554×10 DataFrame
    Row │ 100      200      300      400      500      600      700      800   ⋯
        │ Float64  Float64  Float64  Float64  Float64  Float64  Float64  Float ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │   4.988   23.628   21.87    23.367   25.385   38.641   29.472   47.1 ⋯
      2 │  11.645   16.494   29.382   46.817   58.831   64.859  100.841   78.9
      3 │   0.214    0.038    0.148    0.258    0.522    0.129    0.278    0.4
      4 │   0.42     0.205    0.436    0.733    2.361    2.431    1.533    2.1
      5 │  25.54    55.684   91.336  114.811  152.554  177.244  219.491  243.1 ⋯
      6 │   0.412    1.965    1.184    4.209    1.955    6.086    4.59     0.5
      7 │  18.377   37.331   70.138   84.344  110.532  123.021  153.768  184.0
      8 │  11.209   14.99    32.078   44.26    58.897   65.604  113.114   99.5
      9 │   0.157    5.092    0.226    0.584    0.65     0.379    0.179    0.7 ⋯
     10 │  25.724   45.493   93.7    116.426  151.086  172.583  220.072  267.5
     11 │  25.476   51.47    86.311  116.896  148.888  170.712  223.944  270.2
   ⋮    │    ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋱
 190545 │   0.286    0.751    1.582    1.871    1.586    3.598    3.886    8.4
 190546 │   0.849    2.179    0.657    4.421    5.074    1.565    4.165   12.7 ⋯
 190547 │   0.226    0.108    0.246    0.35     0.851    0.423    0.773    0.2
 190548 │  25.388   63.054   88.711  113.086  150.112  176.971  206.593  251.3
 190549 │  25.059   56.522   82.07   114.199  140.18   164.506  197.914  225.3
 190550 │  25.504   55.064   87.657  114.311  151.9    177.172  215.799  241.8 ⋯
 190551 │  25.818   52.847   79.725  114.079  145.619  175.826  200.24   227.8
 190552 │   0.502    2.549    0.656    1.38     1.773    1.799    4.011    1.4
 190553 │   0.514    0.679    1.864    2.988    2.995    2.032    2.394    2.9
 190554 │   0.322    0.827    0.53     0.678    0.867    3.235    1.649    0.1 ⋯
                                               3 columns and 190533 rows omitted

In [21]:
train_rewards3, train_reward_score3 = get_rewards(reward_lnr_dr_xgb, train_X, train_t_discrete, train_y, t_options)
train_rewards3

190554×10 DataFrame
    Row │ 100       200      300      400       500       600        700       ⋯
        │ Float64   Float64  Float64  Float64   Float64   Float64    Float64   ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │    1.214   28.102    1.433    -2.866     1.63       5.308    0.944   ⋯
      2 │  -62.246   16.482   22.5      38.189    35.119     58.287   76.438
      3 │    0.008    0.04    -0.036     0.043     0.261      0.098    0.069
      4 │    0.009    0.024   -0.033     0.317     1.955      0.101    0.091
      5 │   26.581   71.941  149.828   122.385   236.015   4338.33   497.561   ⋯
      6 │    0.035    0.025    0.086    -2.252     0.041      1.521    0.116
      7 │   48.504    3.498   37.214  -100.584   322.664    127.345   91.038
      8 │    8.862    8.883  -65.047    29.223    61.309     49.355  100.654
      9 │    0.01     0.045    0.026     0.384     0.024     -3.232    0.035   ⋯
     10 │   31.956    9.437  128.818  -267.277   111.611    167.905  133.858
     11 │   22.298   40.718   89.069   114.24    165.09   -1897.49   284.571
   ⋮    │    ⋮         ⋮        ⋮        ⋮         ⋮          ⋮         ⋮      ⋱
 190545 │    0.028    0.01     0.032     0.637    -0.136      0.051    0.097
 190546 │   -0.438    0.024    0.093     1.828     0.068      0.074    0.117   ⋯
 190547 │    0.038    0.146    0.019     0.059     0.038      0.03    -4.236
 190548 │ -135.828   76.655   91.268   120.182   199.984    210.579  176.447
 190549 │   26.881   28.822   63.936    96.093  -430.64     113.114   69.56
 190550 │   26.581   23.346  127.814  -357.15    153.583    169.536  213.809   ⋯
 190551 │   28.902   32.377   64.579    94.278  -521.247    144.361  342.093
 190552 │    0.019    0.14     0.156    -0.133     0.021      0.027    0.068
 190553 │    0.032    0.012    0.031     1.973    -0.413      0.158    0.129
 190554 │    0.018    0.025    0.03     -0.121     0.035      0.099    0.154   ⋯
                                               3 columns and 190533 rows omitted

In [22]:
train_rewards4, train_reward_score4 = get_rewards(reward_lnr_dr_rf, train_X, train_t_discrete, train_y, t_options)
train_rewards4

190554×10 DataFrame
    Row │ 100      200      300      400       500       600        700      8 ⋯
        │ Float64  Float64  Float64  Float64   Float64   Float64    Float64  F ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │   4.988   23.628   21.87    -59.961    25.385     38.641   29.472    ⋯
      2 │ -71.037   16.494   29.382    46.817    58.831     64.859  100.841
      3 │   0.214    0.038   -0.298     0.258     0.522      0.129    0.278
      4 │   0.42     0.205   -1.015     0.733     2.361      2.431    1.533
      5 │  25.54    55.684   91.336   114.811   152.554   4190.44   219.491  2 ⋯
      6 │   0.412    1.965    1.184    -9.199     1.955      6.086    4.59
      7 │  18.377   37.331   70.138  -221.423   110.532    123.021  153.768  1
      8 │  11.209   14.99   -87.892    44.26     58.897     65.604  113.114
      9 │   0.157    5.092    0.226     0.584     0.65      -8.026    0.179    ⋯
     10 │  25.724   45.493   93.7    -255.285   151.086    172.583  220.072  2
     11 │  25.476   51.47    86.311   116.896   148.888  -1629.74   223.944  2
   ⋮    │    ⋮        ⋮        ⋮        ⋮         ⋮          ⋮         ⋮       ⋱
 190545 │   0.286    0.751    1.582     1.871    -6.275      3.598    3.886
 190546 │  -3.196    2.179    0.657     4.421     5.074      1.565    4.165    ⋯
 190547 │   0.226    0.108    0.246     0.35      0.851      0.423  -32.218
 190548 │ -96.628   63.054   88.711   113.086   150.112    176.971  206.593  2
 190549 │  25.059   56.522   82.07    114.199  -477.616    164.506  197.914  2
 190550 │  25.504   55.064   87.657  -295.486   151.9      177.172  215.799  2 ⋯
 190551 │  25.818   52.847   79.725   114.079  -512.551    175.826  200.24   2
 190552 │   0.502    2.549    0.656    -3.398     1.773      1.799    4.011
 190553 │   0.514    0.679    1.864     2.988   -17.083      2.032    2.394
 190554 │   0.322    0.827    0.53     -1.226     0.867      3.235    1.649    ⋯
                                               3 columns and 190533 rows omitted

In [40]:
optimal_policy_grid = IAI.GridSearch(
    IAI.OptimalTreePolicyMaximizer(
      random_seed=seed,
      #localsearch=false,
    ),
    max_depth=1:6,
)
IAI.fit!(optimal_policy_grid, train_X, train_rewards3)

All Grid Results:

 Row │ max_depth  cp          train_score  valid_score  rank_valid_score 
     │ Int64      Float64     Float64      Float64      Int64            
─────┼───────────────────────────────────────────────────────────────────
   1 │         1  3.64067e-5  7.28134e-5   0.000104851                 6
   2 │         2  3.16316e-5  0.000250773  0.000278163                 5
   3 │         3  4.05978e-5  0.000446879  0.000366348                 4
   4 │         4  1.43951e-5  0.000669098  0.000464444                 3
   5 │         5  9.10774e-6  0.000914846  0.000510678                 2
   6 │         6  6.35331e-6  0.00121506   0.000569555                 1

Best Params:
  cp => 6.353307861861612e-6
  max_depth => 6

Best Model - Fitted OptimalTreePolicyMaximizer:
  1) Split: Vintage < 77.5
    2) Split: Gender is Male or is missing
      3) Split: Age < 45.5
        4) Split: Vintage < 23.5
          5) Split: Vintage < 18.5
            6) Prescribe: 900, 1963 points, error 42398.8
            7) Prescribe: 800, 1059 points, error 42263.8
          8) Split: Age < 37.5
            9) Split: Vintage < 43.5
              10) Prescribe: 600, 3259 points, error 42478.3
              11) Prescribe: 800, 5455 points, error 42452.5
            12) Split: Vintage < 54.5
              13) Prescribe: 700, 1966 points, error 42341.1
              14) Prescribe: 1000, 1449 points, error 42177.6
        15) Split: Vintage < 40.5
          16) Split: Vintage < 12.5
            17) Prescribe: 900, 371 points, error 42172.3
            18) Split: Vintage < 31.5
              19) Prescribe: 1000, 2561 points, error 42196.7
              20) Prescribe: 800, 1218 points, error 42331.5
          21) Split: Vintage < 68.5
            22) Prescribe: 900, 3787 points, error 42238.2
            23) Prescribe: 1000, 1235 points, error 42325.9
      24) Split: Vintage < 22.5
        25) Split: Vehicle_Age is 0 or is missing
          26) Prescribe: 700, 1985 points, error 42486.8
          27) Prescribe: 900, 1849 points, error 42206.7
        28) Split: Vintage < 49.5
          29) Split: Vehicle_Age is 0 or is missing
            30) Prescribe: 1000, 4221 points, error 42502.2
            31) Split: Age < 51.5
              32) Prescribe: 700, 2534 points, error 42247.8
              33) Prescribe: 800, 1421 points, error 42386.6
          34) Split: Vintage < 57.5
            35) Prescribe: 900, 2409 points, error 42381.1
            36) Prescribe: 1000, 6005 points, error 42399
    37) Split: Vintage < 251.5
      38) Split: Vintage < 175.5
        39) Split: Age < 45.5
          40) Split: Vintage < 122.5
            41) Split: Vintage < 82.5
              42) Prescribe: 900, 2205 points, error 42430.8
              43) Prescribe: 1000, 17878 points, error 42451.1
            44) Split: Vehicle_Age is 1
              45) Prescribe: 800, 8207 points, error 42297.2
              46) Prescribe: 1000, 15286 points, error 42510.1
          47) Split: Vintage < 149.5
            48) Split: Vehicle_Age in [0,2] or is missing
              49) Prescribe: 800, 1647 points, error 42299.1
              50) Prescribe: 900, 13536 points, error 42375.5
            51) Split: Vintage < 160.5
              52) Prescribe: 1000, 2362 points, error 42287.8
              53) Prescribe: 800, 3076 points, error 42380.8
        54) Split: Age < 24.5
          55) Prescribe: 900, 12327 points, error 42512
          56) Prescribe: 1000, 37593 points, error 42370.9
      57) Split: Vintage < 266.5
        58) Split: Gender is Male or is missing
          59) Split: Age < 65.5
            60) Prescribe: 800, 4888 points, error 42360.1
            61) Prescribe: 700, 422 points, error 42437.2
          62) Prescribe: 700, 4626 points, error 42456.1
        63) Split: Vehicle_Age in [0,1] or is missing
          64) Prescribe: 1000, 20854 points, error 42415.8
          65) Split: Age < 59.5
            66) Prescribe: 900, 591 points, error 42054.6
            6

In [42]:
treatment_pres = IAI.predict(optimal_policy_grid, test_X);

In [43]:
df_w_prescri = hcat(test_X, treatment_pres);
CSV.write("./prescription.csv", df_w_prescri)

"./prescription.csv"

In [41]:
optimal_policy_grid4 = IAI.GridSearch(
    IAI.OptimalTreePolicyMaximizer(
      random_seed=seed,
      #localsearch=false,
    ),
    max_depth=1:6,
)
IAI.fit!(optimal_policy_grid4, train_X, train_rewards4)

All Grid Results:

 Row │ max_depth  cp          train_score  valid_score  rank_valid_score 
     │ Int64      Float64     Float64      Float64      Int64            
─────┼───────────────────────────────────────────────────────────────────
   1 │         1  2.00194e-5  4.00388e-5   0.000103541                 3
   2 │         2  1.96708e-5  7.04313e-5   0.000107523                 2
   3 │         3  1.91925e-5  0.000153455  0.000127573                 1
   4 │         4  2.44058e-5  0.000289423  6.58126e-5                  4
   5 │         5  1.60282e-5  0.000444551  6.40073e-5                  5
   6 │         6  1.56224e-5  0.000633898  5.6952e-5                   6

Best Params:
  cp => 1.9192545008728247e-5
  max_depth => 3

Best Model - Fitted OptimalTreePolicyMaximizer:
  1) Split: Vintage < 20.5
    2) Prescribe: 900, 7018 points, error 39094.4
    3) Split: Vintage < 26.5
      4) Prescribe: 800, 3977 points, error 39114.9
      5) Prescribe: 1000, 179559 points, error 39146.3

### OPT Evaluation

## Real Data

In [46]:
# Get revenue observed for test set in reality
test_revenue = test_y .* test_t;
print("The real life data suggest the annual revenue would be ", sum(test_revenue))
print("\n")

test_t_discrete = [min(round(x, digits=-2), 1000) < 100 ? 100 : min(round(x, digits=-2), 1000) for x in test_t]
test_revenue_cut = test_y .* test_t_discrete;
print("If we do the cutoff on real life data, the annual revenue would be ", sum(test_revenue_cut))

The real life data suggest the annual revenue would be 5.285353428e6
If we do the cutoff on real life data, the annual revenue would be 5.4211e6

## Our Prescription

In [ ]:
test_rewards, test_reward_score = get_rewards(reward_lnr, test_X, test_t,
                                              test_y, t_options)
test_rewards

In [37]:
function evaluate(recommendations, outcomes, actual_revenue)
  n = length(recommendations)
  pred_revenue = [outcomes[i, recommendations[i]] for i in 1:n]

  improvement = mean(pred_revenue .- actual_revenue) / mean(actual_revenue)
end

evaluate (generic function with 1 method)

In [38]:
recommendations_pres = Symbol.(IAI.predict(prescriptive_grid, test_X)[1])
evaluate(recommendations_pres, test_rewards, test_revenue)

LoadError: UndefVarError: `test_rewards` not defined